
# Multistart optimization

Runs simple optimization problem with multiple starting points
Nests an :class:`.MDOScenario` in a :class:`.DOEScenario`
using an :class:`.MDOScenarioAdapter`.


In [ ]:
from __future__ import annotations

from gemseo import configure_logger
from gemseo import create_design_space
from gemseo import create_discipline
from gemseo import create_scenario
from gemseo.disciplines.scenario_adapters.mdo_scenario_adapter import MDOScenarioAdapter

configure_logger()

## Create the disciplines



In [ ]:
objective = create_discipline("AnalyticDiscipline", expressions={"obj": "x**3-x+1"})
constraint = create_discipline(
    "AnalyticDiscipline", expressions={"cstr": "x**2+obj**2-1.5"}
)

## Create the design space



In [ ]:
design_space = create_design_space()
design_space.add_variable("x", l_b=-1.5, u_b=1.5, value=1.5)

## Create the MDO scenario



In [ ]:
scenario = create_scenario(
    [objective, constraint],
    "DisciplinaryOpt",
    "obj",
    design_space,
)
scenario.default_inputs = {"algo": "SLSQP", "max_iter": 10}
scenario.add_constraint("cstr", constraint_type="ineq")

## Create the scenario adapter



In [ ]:
dv_names = scenario.formulation.opt_problem.design_space.variable_names
adapter = MDOScenarioAdapter(
    scenario, dv_names, ["obj", "cstr"], set_x0_before_opt=True
)

## Create the DOE scenario



In [ ]:
scenario_doe = create_scenario(
    adapter,
    "DisciplinaryOpt",
    "obj",
    design_space,
    scenario_type="DOE",
)
scenario_doe.add_constraint("cstr", constraint_type="ineq")
run_inputs = {"n_samples": 10, "algo": "fullfact"}
scenario_doe.execute(run_inputs)

## Plot the optimum objective for different x0



In [ ]:
scenario_doe.post_process("BasicHistory", variable_names=["obj"], save=False, show=True)